In [246]:
import os
import tensorflow as tf
import numpy as np
from IPython.display import Audio
from scipy.io import wavfile

In [3]:
sample_rate, source_audio = wavfile.read("./data/donuts_hq.wav")
sample_start = sample_rate * 60
sample_end = sample_rate * 70
print("Sample rate:", sample_rate)

Sample rate: 32000


In [4]:
Audio(source_audio[sample_start:sample_end], rate=sample_rate)

In [5]:
data_scale = np.amax(np.abs(source_audio))
normalized_audio_data = source_audio / data_scale
train_dataset = tf.data.Dataset.from_tensor_slices(normalized_audio_data)
train_dataset

<TensorSliceDataset shapes: (), types: tf.float64>

In [6]:
DICTIONARY_SAMPLE_SIZE = 3200
assert DICTIONARY_SAMPLE_SIZE == sample_rate // 10
sequences = train_dataset.batch(DICTIONARY_SAMPLE_SIZE, drop_remainder=True)
sequences

<BatchDataset shapes: (3200,), types: tf.float64>

In [7]:
def split_input_target(sequence):
    return sequence, sequence

prepared_dataset = sequences.map(split_input_target)
prepared_dataset

<MapDataset shapes: ((3200,), (3200,)), types: (tf.float64, tf.float64)>

In [8]:
BATCH_SIZE = 32
BUFFER_SIZE = 1024
shuffled_dataset = (
    prepared_dataset
#     .shuffle(BUFFER_SIZE)
    .batch(BATCH_SIZE, drop_remainder=True)
)

In [9]:
CHECKPOINT_DIR = "./training-checkpoints/music-dictionary"

In [10]:
class RoundingSigmoid(tf.keras.layers.Layer):
    def call(self, inputs):
        return tf.math.round(tf.math.sigmoid(inputs))


def softargmax(x, beta=1e10):
    x = tf.convert_to_tensor(x)
    x_range = tf.range(x.shape.as_list()[-1], dtype=x.dtype)
    return tf.reduce_sum(tf.nn.softmax(x * beta) * x_range, axis=-1)


class OneHot(tf.keras.layers.Layer):
    def call(self, inputs):
        x = tf.convert_to_tensor(inputs)
        return tf.nn.softmax(x * 1e10)

# onehot = OneHotSigmoid(5)
# onehot.call([0.1, 0.001, 0.01])
# softargmax([0.9, 0.1, 0.99])

In [11]:
latest_checkpoint = tf.train.latest_checkpoint(CHECKPOINT_DIR)
LATENT_OUTPUT_SIZE = 32

full_model = tf.keras.Sequential([
    tf.keras.layers.InputLayer(
        batch_size=BATCH_SIZE,
        input_shape=(DICTIONARY_SAMPLE_SIZE,),
        dtype="float32",
        name="full_input",
    ),
    tf.keras.layers.Dense(
        DICTIONARY_SAMPLE_SIZE,
        dtype="float32",
        name="dense_1",
    ),
    tf.keras.layers.PReLU(name="prelu_1"),
#     tf.keras.layers.Dense(
#         DICTIONARY_SAMPLE_SIZE,
#         dtype="float32",
#         name="dense_2",
#     ),
#     tf.keras.layers.PReLU(name="prelu_2"),
    tf.keras.layers.Dense(
        LATENT_OUTPUT_SIZE,
        dtype="float32",
        name="dense_3",
    ),
    RoundingSigmoid(
        name="latent_output",
    ),
    tf.keras.layers.Dense(
        DICTIONARY_SAMPLE_SIZE,
        dtype="float32",
        name="dense_4",
    ),
    tf.keras.layers.PReLU(name="prelu_3"),
    tf.keras.layers.Dense(
        DICTIONARY_SAMPLE_SIZE,
        dtype="float32",
        name="dense_5",
    ),
    tf.keras.layers.Activation(
        tf.keras.activations.tanh,
        name="full_output",
    ),
], name="Autoclassifier")
full_model.build()

if latest_checkpoint:
    full_model.load_weights(latest_checkpoint)

full_model.summary()
full_model.compile("adam", loss=tf.keras.losses.MSE)

Model: "Autoclassifier"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (32, 3200)                10243200  
_________________________________________________________________
prelu_1 (PReLU)              (32, 3200)                3200      
_________________________________________________________________
dense_3 (Dense)              (32, 32)                  102432    
_________________________________________________________________
latent_output (RoundingSigmo (32, 32)                  0         
_________________________________________________________________
dense_4 (Dense)              (32, 3200)                105600    
_________________________________________________________________
prelu_3 (PReLU)              (32, 3200)                3200      
_________________________________________________________________
dense_5 (Dense)              (32, 3200)             

In [12]:
encoder = tf.keras.Sequential([
    tf.keras.layers.InputLayer(
        batch_size=BATCH_SIZE,
        input_shape=(DICTIONARY_SAMPLE_SIZE,),
        dtype="float32",
    ),
    full_model.get_layer("dense_1"),
    full_model.get_layer("prelu_1"),
#     full_model.get_layer("dense_2"),
#     full_model.get_layer("prelu_2"),
    full_model.get_layer("dense_3"),
    full_model.get_layer("latent_output"),
], name="Encoder")
encoder.build()
encoder.summary()

Model: "Encoder"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (32, 3200)                10243200  
_________________________________________________________________
prelu_1 (PReLU)              (32, 3200)                3200      
_________________________________________________________________
dense_3 (Dense)              (32, 32)                  102432    
_________________________________________________________________
latent_output (RoundingSigmo (32, 32)                  0         
Total params: 10,348,832
Trainable params: 10,348,832
Non-trainable params: 0
_________________________________________________________________


In [13]:
decoder = tf.keras.Sequential([
    tf.keras.layers.InputLayer(
        batch_size=BATCH_SIZE,
        input_shape=(LATENT_OUTPUT_SIZE,),
        dtype="float32",
    ),
    full_model.get_layer("dense_4"),
    full_model.get_layer("prelu_3"),
    full_model.get_layer("dense_5"),
    full_model.get_layer("full_output"),
], name="Decoder")
decoder.build()
decoder.summary()

Model: "Decoder"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_4 (Dense)              (32, 3200)                105600    
_________________________________________________________________
prelu_3 (PReLU)              (32, 3200)                3200      
_________________________________________________________________
dense_5 (Dense)              (32, 3200)                10243200  
_________________________________________________________________
full_output (Activation)     (32, 3200)                0         
Total params: 10,352,000
Trainable params: 10,352,000
Non-trainable params: 0
_________________________________________________________________


In [127]:
checkpoint_prefix = os.path.abspath(
    os.path.join(CHECKPOINT_DIR, "ckpt_{epoch}")
)

checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_prefix,
    save_weights_only=True,
    monitor="loss",
    save_best_only=True,
    period=100,
)

In [15]:
from notebooks.tf.scheduler import SGDRScheduler

learningrate_callback = SGDRScheduler(
    min_lr=1e-5,
    max_lr=1e-2,
    steps_per_epoch=54,
    lr_decay=0.9,
    cycle_length=5,
    mult_factor=1.5
)

In [58]:
EPOCHS = 10000
history = full_model.fit(
    shuffled_dataset,
    epochs=EPOCHS,
    callbacks=[
        checkpoint_callback,
        learningrate_callback,
    ],
)

Train for 54 steps
Epoch 1/10000
54/54 [==============================] - 5s 94ms/step - loss: 0.0452
Epoch 2/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0472
Epoch 3/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0442
Epoch 4/10000
54/54 [==============================] - 5s 93ms/step - loss: 0.0397
Epoch 5/10000
54/54 [==============================] - 5s 97ms/step - loss: 0.0358
Epoch 6/10000
54/54 [==============================] - 5s 97ms/step - loss: 0.0414
Epoch 7/10000
54/54 [==============================] - 7s 136ms/step - loss: 0.0438
Epoch 8/10000
54/54 [==============================] - 6s 115ms/step - loss: 0.0424
Epoch 9/10000
54/54 [==============================] - 6s 108ms/step - loss: 0.0399
Epoch 10/10000
54/54 [==============================] - 6s 107ms/step - loss: 0.0374
Epoch 11/10000
54/54 [==============================] - 6s 103ms/step - loss: 0.0348
Epoch 12/10000
54/54 [==============================] - 5s 10

54/54 [==============================] - 5s 95ms/step - loss: 0.0108
Epoch 194/10000
54/54 [==============================] - 5s 96ms/step - loss: 0.0110
Epoch 195/10000
54/54 [==============================] - 5s 95ms/step - loss: 0.0109
Epoch 196/10000
54/54 [==============================] - 5s 95ms/step - loss: 0.0095
Epoch 197/10000
54/54 [==============================] - 5s 95ms/step - loss: 0.0091
Epoch 198/10000
54/54 [==============================] - 5s 94ms/step - loss: 0.0088
Epoch 199/10000
54/54 [==============================] - 5s 93ms/step - loss: 0.0091
Epoch 200/10000
54/54 [==============================] - 9s 162ms/step - loss: 0.0092
Epoch 201/10000
54/54 [==============================] - 5s 96ms/step - loss: 0.0092
Epoch 202/10000
54/54 [==============================] - 5s 93ms/step - loss: 0.0086
Epoch 203/10000
54/54 [==============================] - 5s 96ms/step - loss: 0.0086
Epoch 204/10000
54/54 [==============================] - 5s 96ms/step - loss: 0.

54/54 [==============================] - 5s 92ms/step - loss: 0.0017
Epoch 386/10000
54/54 [==============================] - 5s 91ms/step - loss: 0.0017
Epoch 387/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0017
Epoch 388/10000
54/54 [==============================] - 5s 90ms/step - loss: 0.0017
Epoch 389/10000
54/54 [==============================] - 5s 91ms/step - loss: 0.0017
Epoch 390/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0017
Epoch 391/10000
54/54 [==============================] - 5s 93ms/step - loss: 0.0017
Epoch 392/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0017
Epoch 393/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0017
Epoch 394/10000
54/54 [==============================] - 5s 91ms/step - loss: 0.0016
Epoch 395/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0016
Epoch 396/10000
54/54 [==============================] - 5s 91ms/step - loss: 0.0

54/54 [==============================] - 6s 113ms/step - loss: 0.0014
Epoch 578/10000
54/54 [==============================] - 6s 112ms/step - loss: 0.0014
Epoch 579/10000
54/54 [==============================] - 6s 114ms/step - loss: 0.0014
Epoch 580/10000
54/54 [==============================] - 6s 116ms/step - loss: 0.0014
Epoch 581/10000
54/54 [==============================] - 7s 126ms/step - loss: 0.0013
Epoch 582/10000
54/54 [==============================] - 6s 117ms/step - loss: 0.0013
Epoch 583/10000
54/54 [==============================] - 7s 123ms/step - loss: 0.0013
Epoch 584/10000
54/54 [==============================] - 6s 113ms/step - loss: 0.0013
Epoch 585/10000
54/54 [==============================] - 6s 119ms/step - loss: 0.0013
Epoch 586/10000
54/54 [==============================] - 6s 116ms/step - loss: 0.0013
Epoch 587/10000
54/54 [==============================] - 7s 131ms/step - loss: 0.0013
Epoch 588/10000
54/54 [==============================] - 6s 114ms/step

54/54 [==============================] - 6s 117ms/step - loss: 0.0038
Epoch 768/10000
54/54 [==============================] - 7s 126ms/step - loss: 0.0039
Epoch 769/10000
54/54 [==============================] - 5s 98ms/step - loss: 0.0038
Epoch 770/10000
54/54 [==============================] - 7s 125ms/step - loss: 0.0038
Epoch 771/10000
54/54 [==============================] - 6s 113ms/step - loss: 0.0037
Epoch 772/10000
54/54 [==============================] - 7s 122ms/step - loss: 0.0037
Epoch 773/10000
54/54 [==============================] - 6s 111ms/step - loss: 0.0037
Epoch 774/10000
54/54 [==============================] - 7s 128ms/step - loss: 0.0038
Epoch 775/10000
54/54 [==============================] - 7s 126ms/step - loss: 0.0040
Epoch 776/10000
54/54 [==============================] - 6s 118ms/step - loss: 0.0040
Epoch 777/10000
54/54 [==============================] - 6s 120ms/step - loss: 0.0037
Epoch 778/10000
54/54 [==============================] - 6s 113ms/step 

...

54/54 [==============================] - 6s 119ms/step - loss: 0.0031
Epoch 5933/10000
54/54 [==============================] - 7s 131ms/step - loss: 0.0030
Epoch 5934/10000
54/54 [==============================] - 7s 131ms/step - loss: 0.0030
Epoch 5935/10000
54/54 [==============================] - 6s 118ms/step - loss: 0.0029
Epoch 5936/10000
54/54 [==============================] - 7s 127ms/step - loss: 0.0030
Epoch 5937/10000
54/54 [==============================] - 6s 117ms/step - loss: 0.0029
Epoch 5938/10000
54/54 [==============================] - 7s 124ms/step - loss: 0.0029
Epoch 5939/10000
54/54 [==============================] - 7s 125ms/step - loss: 0.0029
Epoch 5940/10000
54/54 [==============================] - 6s 117ms/step - loss: 0.0029
Epoch 5941/10000
54/54 [==============================] - 6s 114ms/step - loss: 0.0028
Epoch 5942/10000
54/54 [==============================] - 6s 116ms/step - loss: 0.0027
Epoch 5943/10000
54/54 [==============================] - 7s

54/54 [==============================] - 5s 93ms/step - loss: 0.0024
Epoch 6121/10000
54/54 [==============================] - 5s 94ms/step - loss: 0.0025
Epoch 6122/10000
54/54 [==============================] - 5s 93ms/step - loss: 0.0024
Epoch 6123/10000
54/54 [==============================] - 5s 95ms/step - loss: 0.0024
Epoch 6124/10000
54/54 [==============================] - 6s 105ms/step - loss: 0.0024
Epoch 6125/10000
54/54 [==============================] - 5s 94ms/step - loss: 0.0024
Epoch 6126/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0027
Epoch 6127/10000
54/54 [==============================] - 5s 96ms/step - loss: 0.0028
Epoch 6128/10000
54/54 [==============================] - 6s 104ms/step - loss: 0.0029
Epoch 6129/10000
54/54 [==============================] - 5s 94ms/step - loss: 0.0027
Epoch 6130/10000
54/54 [==============================] - 5s 99ms/step - loss: 0.0026
Epoch 6131/10000
54/54 [==============================] - 5s 94ms/ste

54/54 [==============================] - 5s 91ms/step - loss: 0.0016
Epoch 6311/10000
54/54 [==============================] - 5s 100ms/step - loss: 0.0015
Epoch 6312/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0015
Epoch 6313/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0014
Epoch 6314/10000
54/54 [==============================] - 5s 92ms/step - loss: 0.0014
Epoch 6315/10000
54/54 [==============================] - 5s 95ms/step - loss: 0.0015
Epoch 6316/10000
54/54 [==============================] - 5s 93ms/step - loss: 0.0015
Epoch 6317/10000
54/54 [==============================] - 5s 94ms/step - loss: 0.0015
Epoch 6318/10000
54/54 [==============================] - 5s 93ms/step - loss: 0.0015
Epoch 6319/10000
54/54 [==============================] - 5s 95ms/step - loss: 0.0015
Epoch 6320/10000
54/54 [==============================] - 5s 93ms/step - loss: 0.0015
Epoch 6321/10000
54/54 [==============================] - 5s 92ms/step

54/54 [==============================] - 5s 97ms/step - loss: 0.0014
Epoch 6406/10000
54/54 [==============================] - 5s 95ms/step - loss: 0.0014
Epoch 6407/10000
54/54 [==============================] - 5s 99ms/step - loss: 0.0014
Epoch 6408/10000
54/54 [==============================] - 5s 96ms/step - loss: 0.0013
Epoch 6409/10000
54/54 [==============================] - 5s 97ms/step - loss: 0.0013
Epoch 6410/10000
54/54 [==============================] - 5s 96ms/step - loss: 0.0013
Epoch 6411/10000
54/54 [==============================] - 6s 111ms/step - loss: 0.0013
Epoch 6412/10000
54/54 [==============================] - 6s 108ms/step - loss: 0.0013
Epoch 6413/10000
54/54 [==============================] - 6s 113ms/step - loss: 0.0013
Epoch 6414/10000
54/54 [==============================] - 6s 103ms/step - loss: 0.0013
Epoch 6415/10000
54/54 [==============================] - 6s 104ms/step - loss: 0.0013
Epoch 6416/10000
54/54 [==============================] - 6s 103ms

KeyboardInterrupt: 

In [16]:
batched_samples = sequences.batch(32, drop_remainder=True)
sample = list(batched_samples.take(1))[0]
Audio(sample.numpy().flatten() * data_scale, rate=sample_rate)

In [17]:
result = full_model(sample).numpy().flatten() * data_scale

In [18]:
Audio(result, rate=sample_rate)

In [19]:
encoded = encoder(sample)
result = decoder(encoded).numpy().flatten() * data_scale
Audio(result, rate=sample_rate)

In [20]:
full_result = []
for entry in batched_samples:
    result = full_model(entry).numpy().flatten() * data_scale
    full_result.extend(result)

In [21]:
Audio(full_result[:sample_rate * 10], rate=sample_rate)

In [73]:
audio_dictionary = set()
total_entries = 0

for entry in batched_samples:
    result = encoder(entry).numpy()
    bool_result = result.astype(np.bool)
    for batch in bool_result:
        audio_dictionary.add(tuple(batch))
        total_entries += 1

print(total_entries)
print(len(audio_dictionary))

1728
1672


In [140]:
int_to_audio = {
    index: signature
    for index, signature in enumerate(audio_dictionary)
}
audio_to_int = {
    signature: index
    for index, signature in enumerate(audio_dictionary)
}

In [216]:
def extend_audio_dictionary(signature):
    index = len(int_to_audio)
    int_to_audio[index] = signature
    audio_to_int[signature] = index


def convert_audio_to_integers(audio, sample_rate):
    normalized = audio / data_scale
    assert sample_rate == 32000
    batched = (
        tf.data.Dataset.from_tensor_slices(normalized)
        .batch(DICTIONARY_SAMPLE_SIZE, drop_remainder=True)
        .batch(BATCH_SIZE, drop_remainder=True)
    )
    result = []
    for batch in batched:
        encoded = encoder(batch).numpy().astype(np.bool)
        for entry in encoded:
            key = tuple(entry)
            if key not in audio_to_int:
                extend_audio_dictionary(key)
            result.append(audio_to_int[key])
    return result

def convert_integer_to_audio_signature(integer):
    signature = int_to_audio[integer]
    array = np.array(signature, dtype=np.bool)
    final = array.astype(np.float32)
    return final

def convert_integers_to_audio(integers):
    signatures = [convert_integer_to_audio_signature(x) for x in integers]
    batched = (
        tf.data.Dataset.from_tensor_slices(signatures)
        .batch(LATENT_OUTPUT_SIZE, drop_remainder=True)
    )
    result = []
    for batch in batched:
        decoded = decoder(batch).numpy().flatten()
        result.extend(decoded)
    return np.array(result) * data_scale

In [89]:
integerified_audio = convert_audio_to_integers(source_audio, sample_rate)

In [90]:
print(len(integerified_audio))

1728


In [91]:
audiofied_integers = convert_integers_to_audio(integerified_audio)

In [92]:
Audio(audiofied_integers[sample_start:sample_end], rate=sample_rate)

In [70]:
test = convert_integers_to_audio(int_to_audio.keys())
Audio(test[sample_start:sample_end], rate=sample_rate)

In [66]:
_, unknown_audio = wavfile.read("./data/feelsogood_hq.wav")
unknown_integers = convert_audio_to_integers(unknown_audio, sample_rate)
unknown_audio = convert_integers_to_audio(unknown_integers)

In [71]:
Audio(unknown_audio[sample_start:sample_end], rate=sample_rate)

In [207]:
rnn_checkpoint_dir = "./training-checkpoints/audio-dictionary-rnn"
last_rnn_checkpoint = tf.train.latest_checkpoint(rnn_checkpoint_dir)

RNN_UNITS = 1024
EMBEDDING_UNITS = 64
VOCABULARY_SIZE = len(int_to_audio)

def build_rnn(vocabulary_size, embedding_dimension, rnn_units, batch_size):
    model = tf.keras.Sequential([
        tf.keras.layers.Embedding(
            vocabulary_size,
            embedding_dimension,
            batch_input_shape=[batch_size, None],
            name="embedding",
        ),
        tf.keras.layers.GRU(
            rnn_units,
            return_sequences=True,
            stateful=True,
            recurrent_initializer="glorot_uniform",
            name="gru",
        ),
        tf.keras.layers.Dense(
            vocabulary_size,
            name="out",
        ),
    ], "RNN")
    return model

rnn = build_rnn(
    vocabulary_size=VOCABULARY_SIZE,
    embedding_dimension=EMBEDDING_UNITS,
    rnn_units=RNN_UNITS,
    batch_size=BATCH_SIZE,
)
if last_rnn_checkpoint:
    print("Loaded!")
    rnn.load_weights(last_rnn_checkpoint)

# rnn.build()
rnn.summary()

def rnn_loss(labels, logits):
    return tf.keras.losses.sparse_categorical_crossentropy(
        labels,
        logits,
        from_logits=True,
    )

rnn.compile("adam", loss=rnn_loss)

Loaded!
Model: "RNN"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (32, None, 64)            107008    
_________________________________________________________________
gru (GRU)                    (32, None, 1024)          3348480   
_________________________________________________________________
out (Dense)                  (32, None, 1672)          1713800   
Total params: 5,169,288
Trainable params: 5,169,288
Non-trainable params: 0
_________________________________________________________________


In [208]:
RNN_SEQUENCE_LENGTH = 10

rnn_dataset = tf.data.Dataset.from_tensor_slices(integerified_audio)
rnn_sequences = rnn_dataset.batch(
    RNN_SEQUENCE_LENGTH + 1,
    drop_remainder=True
)

def split_input_target(sequence):
    input_data = sequence[:-1]
    target_data = sequence[1:]
    return input_data, target_data

rnn_sequences = rnn_sequences.map(split_input_target)
rnn_sequences

<MapDataset shapes: ((10,), (10,)), types: (tf.int32, tf.int32)>

In [209]:
rnn_training_data = (
    rnn_sequences
    .shuffle(BUFFER_SIZE)
    .batch(BATCH_SIZE, drop_remainder=True)
)

rnn_training_data

<BatchDataset shapes: ((32, 10), (32, 10)), types: (tf.int32, tf.int32)>

In [217]:
dataset_test_samples = list(rnn_training_data.take(4))
test_data = test_sampels[0][0].numpy().flatten()
test_data = np.concatenate((asd, test_sampels[1][0].numpy().flatten()))
test_data = np.concatenate((asd, test_sampels[2][0].numpy().flatten()))
test_data = np.concatenate((asd, test_sampels[3][0].numpy().flatten()))
test_audio = convert_integers_to_audio(asd)

In [218]:
Audio(test_audio[sample_start:sample_end], rate=sample_rate)

In [212]:
rnn_checkpoint_prefix = os.path.abspath(
    os.path.join(rnn_checkpoint_dir, "ckpt_{epoch}")
)

rnn_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=rnn_checkpoint_prefix,
    save_weights_only=True,
    monitor="loss",
    save_best_only=True,
    period=100,
)

In [213]:
from notebooks.tf.scheduler import SGDRScheduler

rnn_lr_schedule = SGDRScheduler(
    min_lr=1e-5,
    max_lr=1e-2,
    steps_per_epoch=54,
    lr_decay=0.9,
    cycle_length=5,
    mult_factor=1.5
)

In [214]:
EPOCHS = 1000
history = rnn.fit(
    rnn_training_data,
    epochs=EPOCHS,
    callbacks=[
        rnn_checkpoint_callback,
        rnn_lr_schedule,
    ],
)

Train for 4 steps
Epoch 1/1000
4/4 [==============================] - 1s 279ms/step - loss: 5.4482e-04
Epoch 2/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0316
Epoch 3/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0905
Epoch 4/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.1531
Epoch 5/1000
4/4 [==============================] - 0s 24ms/step - loss: 0.5802
Epoch 6/1000
4/4 [==============================] - 0s 20ms/step - loss: 1.7814
Epoch 7/1000
4/4 [==============================] - 0s 20ms/step - loss: 2.2470
Epoch 8/1000
4/4 [==============================] - 0s 19ms/step - loss: 3.5736
Epoch 9/1000
4/4 [==============================] - 0s 20ms/step - loss: 3.4071
Epoch 10/1000
4/4 [==============================] - 0s 21ms/step - loss: 3.3106
Epoch 11/1000
4/4 [==============================] - 0s 19ms/step - loss: 3.1789
Epoch 12/1000
4/4 [==============================] - 0s 19ms/step - loss: 3.0005
Epoch 13/1000


4/4 [==============================] - 0s 23ms/step - loss: 0.0115
Epoch 102/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0021
Epoch 103/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0083
Epoch 104/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0178
Epoch 105/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0052
Epoch 106/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0092
Epoch 107/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0151
Epoch 108/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0132
Epoch 109/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0061
Epoch 110/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0022
Epoch 111/1000
4/4 [==============================] - 0s 25ms/step - loss: 0.0229
Epoch 112/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0228
Epoch 113/1000
4/4 [===========

4/4 [==============================] - 0s 19ms/step - loss: 0.0094
Epoch 201/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0022
Epoch 202/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0066
Epoch 203/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0069
Epoch 204/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0058
Epoch 205/1000
4/4 [==============================] - 0s 20ms/step - loss: 4.1096e-04
Epoch 206/1000
4/4 [==============================] - 0s 19ms/step - loss: 7.8342e-04
Epoch 207/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0100
Epoch 208/1000
4/4 [==============================] - 0s 20ms/step - loss: 2.4832e-04
Epoch 209/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0011
Epoch 210/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0026
Epoch 211/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0018
Epoch 212/1000
4/4 

4/4 [==============================] - 0s 19ms/step - loss: 0.0102
Epoch 298/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0113
Epoch 299/1000
4/4 [==============================] - 0s 18ms/step - loss: 1.0236e-05
Epoch 300/1000
4/4 [==============================] - 1s 359ms/step - loss: 3.1020e-05
Epoch 301/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0012
Epoch 302/1000
4/4 [==============================] - 0s 19ms/step - loss: 1.2069e-05
Epoch 303/1000
4/4 [==============================] - 0s 19ms/step - loss: 4.2548e-06
Epoch 304/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0033
Epoch 305/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0013
Epoch 306/1000
4/4 [==============================] - 0s 20ms/step - loss: 5.3084e-06
Epoch 307/1000
4/4 [==============================] - 0s 19ms/step - loss: 5.2684e-04
Epoch 308/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0039
Epoch 

4/4 [==============================] - 0s 19ms/step - loss: 5.4987e-04
Epoch 396/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0022
Epoch 397/1000
4/4 [==============================] - 0s 18ms/step - loss: 4.1952e-04
Epoch 398/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0021
Epoch 399/1000
4/4 [==============================] - 0s 19ms/step - loss: 3.6815e-04
Epoch 400/1000
4/4 [==============================] - 0s 19ms/step - loss: 8.4968e-05
Epoch 401/1000
4/4 [==============================] - 0s 18ms/step - loss: 6.2330e-04
Epoch 402/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0022
Epoch 403/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0127
Epoch 404/1000
4/4 [==============================] - 0s 19ms/step - loss: 2.5193e-06
Epoch 405/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0011
Epoch 406/1000
4/4 [==============================] - 0s 24ms/step - loss: 9.0839e-05
Epo

...

4/4 [==============================] - 0s 18ms/step - loss: 2.4482e-04
Epoch 590/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0082
Epoch 591/1000
4/4 [==============================] - 0s 19ms/step - loss: 9.9656e-04
Epoch 592/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0030
Epoch 593/1000
4/4 [==============================] - 0s 19ms/step - loss: 2.3113e-05
Epoch 594/1000
4/4 [==============================] - 0s 18ms/step - loss: 1.7961e-06
Epoch 595/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0032
Epoch 596/1000
4/4 [==============================] - 0s 18ms/step - loss: 3.9782e-04
Epoch 597/1000
4/4 [==============================] - 0s 18ms/step - loss: 6.4867e-04
Epoch 598/1000
4/4 [==============================] - 0s 18ms/step - loss: 3.0382e-05
Epoch 599/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0022
Epoch 600/1000
4/4 [==============================] - 0s 19ms/step - loss: 6.7533e-05

4/4 [==============================] - 0s 19ms/step - loss: 4.9676e-05
Epoch 687/1000
4/4 [==============================] - 0s 19ms/step - loss: 3.2220e-04
Epoch 688/1000
4/4 [==============================] - 0s 19ms/step - loss: 2.0619e-04
Epoch 689/1000
4/4 [==============================] - 0s 19ms/step - loss: 6.1131e-06
Epoch 690/1000
4/4 [==============================] - 0s 19ms/step - loss: 2.7836e-04
Epoch 691/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0017
Epoch 692/1000
4/4 [==============================] - 0s 19ms/step - loss: 2.4841e-04
Epoch 693/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0025
Epoch 694/1000
4/4 [==============================] - 0s 19ms/step - loss: 1.2692e-04
Epoch 695/1000
4/4 [==============================] - 0s 19ms/step - loss: 7.5328e-05
Epoch 696/1000
4/4 [==============================] - 0s 18ms/step - loss: 8.9980e-05
Epoch 697/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.

4/4 [==============================] - 0s 19ms/step - loss: 2.3941e-05
Epoch 784/1000
4/4 [==============================] - 0s 19ms/step - loss: 8.0316e-06
Epoch 785/1000
4/4 [==============================] - 0s 19ms/step - loss: 8.6737e-04
Epoch 786/1000
4/4 [==============================] - 0s 19ms/step - loss: 8.3593e-07
Epoch 787/1000
4/4 [==============================] - 0s 19ms/step - loss: 3.5487e-05
Epoch 788/1000
4/4 [==============================] - 0s 18ms/step - loss: 9.6024e-05
Epoch 789/1000
4/4 [==============================] - 0s 18ms/step - loss: 0.0025
Epoch 790/1000
4/4 [==============================] - 0s 18ms/step - loss: 1.6008e-05
Epoch 791/1000
4/4 [==============================] - 0s 19ms/step - loss: 1.5754e-05
Epoch 792/1000
4/4 [==============================] - 0s 19ms/step - loss: 2.4578e-04
Epoch 793/1000
4/4 [==============================] - 0s 19ms/step - loss: 4.5474e-06
Epoch 794/1000
4/4 [==============================] - 0s 18ms/step - loss

4/4 [==============================] - 0s 19ms/step - loss: 0.0019
Epoch 881/1000
4/4 [==============================] - 0s 19ms/step - loss: 7.0933e-04
Epoch 882/1000
4/4 [==============================] - 0s 19ms/step - loss: 7.7423e-04
Epoch 883/1000
4/4 [==============================] - 0s 18ms/step - loss: 8.4075e-04
Epoch 884/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0079
Epoch 885/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0013
Epoch 886/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0081
Epoch 887/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0026
Epoch 888/1000
4/4 [==============================] - 0s 20ms/step - loss: 8.6580e-04
Epoch 889/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0060
Epoch 890/1000
4/4 [==============================] - 0s 21ms/step - loss: 1.9213e-04
Epoch 891/1000
4/4 [==============================] - 0s 21ms/step - loss: 0.0176
Epoch 892/1

Epoch 978/1000
4/4 [==============================] - 0s 19ms/step - loss: 0.0071
Epoch 979/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0091
Epoch 980/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0042
Epoch 981/1000
4/4 [==============================] - 0s 20ms/step - loss: 4.3128e-05
Epoch 982/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0083
Epoch 983/1000
4/4 [==============================] - 0s 21ms/step - loss: 0.0011
Epoch 984/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0049
Epoch 985/1000
4/4 [==============================] - 0s 20ms/step - loss: 0.0129
Epoch 986/1000
4/4 [==============================] - 0s 21ms/step - loss: 0.0020
Epoch 987/1000
4/4 [==============================] - 0s 20ms/step - loss: 6.1193e-06
Epoch 988/1000
4/4 [==============================] - 0s 20ms/step - loss: 3.0229e-04
Epoch 989/1000
4/4 [==============================] - 0s 20ms/step - loss: 9.1067e-04


In [222]:
rnn_generator = build_rnn(
    vocabulary_size=VOCABULARY_SIZE,
    embedding_dimension=EMBEDDING_UNITS,
    rnn_units=RNN_UNITS,
    batch_size=1,
)
rnn_generator.load_weights(tf.train.latest_checkpoint(rnn_checkpoint_dir))
rnn_generator.build()
rnn_generator.summary()

Model: "RNN"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (1, None, 64)             107008    
_________________________________________________________________
gru (GRU)                    (1, None, 1024)           3348480   
_________________________________________________________________
out (Dense)                  (1, None, 1672)           1713800   
Total params: 5,169,288
Trainable params: 5,169,288
Non-trainable params: 0
_________________________________________________________________


In [241]:
def generate_audio_integers(model, input_eval, count=3200):
    generated_output = []
    
    temperature = 1.0
    
    input_eval = tf.expand_dims(input_eval, 0)
    
    model.reset_states()
    for i in range(count):
        predictions = model(input_eval)
        predictions = tf.squeeze(predictions, 0)

        predictions /= temperature
        predicted_id = tf.random.categorical(predictions, num_samples=1)
        predicted_id = predicted_id[-1, 0].numpy()
        
        # Pass in the predicted character as input on the next round
        input_eval = tf.expand_dims([predicted_id], 0)
        generated_output.append(predicted_id)
    
    return generated_output

In [252]:
generated = generate_audio_integers(rnn_generator, range(10), count=320)
audio_data = convert_integers_to_audio(generated)
print(audio_data.shape)

(1024000,)


In [253]:
Audio(audio_data, rate=sample_rate)